<a href="https://colab.research.google.com/github/mapmatters/coursera-nlp/blob/main/nlp_class_1_Week4_nb03_assignment_(naive_machine_translation).ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [101]:
from google.colab import drive
drive.mount('/content/drive')
import os
os.chdir('/content/drive/MyDrive/coursera/nlp')
!ls

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
 data
'nlp class 1 - Week1 - nb01'
'nlp class 1 - Week1 - nb02'
'nlp class 1 - Week1 - nb03'
'nlp class 1 - Week1 - nb04 - assignment'
'nlp class 1 - Week2 - nb01'
'nlp class 1 - Week2 - nb02 - assignment'
'nlp class 1 - Week3 - nb01 - linear algebra'
'nlp class 1 - Week3 - nb02- manipulating word embedding'
'nlp class 1 - Week3 - nb03- PCA.ipynb'
'nlp class 1 - Week3 - nb04 - assignment'
'nlp class 1 - Week4 - nb01 - vector manipulation'
'nlp class 1 - Week4 - nb02 - hash function'
'nlp class 1 - Week4 - nb03 - assignment (naive machine translation)'
 py
 __pycache__


In [103]:
import pdb
import pickle
import string

import time

import gensim
import matplotlib.pyplot as plt
import nltk
import numpy as np
import scipy
import sklearn
from gensim.models import KeyedVectors
from nltk.corpus import stopwords, twitter_samples
from nltk.tokenize import TweetTokenizer
from os import getcwd

## load necessary functions

In [104]:

import re
import string

import numpy as np
import pandas as pd
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.tokenize import TweetTokenizer


def process_tweet(tweet):
    '''
    Input:
        tweet: a string containing a tweet
    Output:
        tweets_clean: a list of words containing the processed tweet

    '''
    stemmer = PorterStemmer()
    stopwords_english = stopwords.words('english')
    # remove stock market tickers like $GE
    tweet = re.sub(r'\$\w*', '', tweet)
    # remove old style retweet text "RT"
    tweet = re.sub(r'^RT[\s]+', '', tweet)
    # remove hyperlinks
    tweet = re.sub(r'https?:\/\/.*[\r\n]*', '', tweet)
    # remove hashtags
    # only removing the hash # sign from the word
    tweet = re.sub(r'#', '', tweet)
    # tokenize tweets
    tokenizer = TweetTokenizer(preserve_case=False, strip_handles=True,
                               reduce_len=True)
    tweet_tokens = tokenizer.tokenize(tweet)

    tweets_clean = []
    for word in tweet_tokens:
        if (word not in stopwords_english and  # remove stopwords
            word not in string.punctuation):  # remove punctuation
            # tweets_clean.append(word)
            stem_word = stemmer.stem(word)  # stemming word
            tweets_clean.append(stem_word)

    return tweets_clean


def get_dict(file_name):
    """
    This function returns the english to french dictionary given a file where the each column corresponds to a word.
    Check out the files this function takes in your workspace.
    """
    my_file = pd.read_csv(file_name, delimiter=' ')
    etof = {}  # the english to french dictionary to be returned
    for i in range(len(my_file)):
        # indexing into the rows.
        en = my_file.loc[i][0]
        fr = my_file.loc[i][1]
        etof[en] = fr

    return etof


def cosine_similarity(A, B):
    '''
    Input:
        A: a numpy array which corresponds to a word vector
        B: A numpy array which corresponds to a word vector
    Output:
        cos: numerical number representing the cosine similarity between A and B.
    '''
    # you have to set this variable to the true label.
    cos = -10
    dot = np.dot(A, B)
    norma = np.linalg.norm(A)
    normb = np.linalg.norm(B)
    cos = dot / (norma * normb)

    return cos


In [105]:
# add folder, tmp2, from our local workspace containing pre-downloaded corpora files to nltk's data path
filePath = f"{getcwd()}/../tmp2/"
nltk.data.path.append(filePath)

# 1. The word embeddings data for English and French words

Write a program that translates English to French.

## The data

The full dataset for English embeddings is about 3.64 gigabytes, and the French
embeddings are about 629 megabytes. To prevent the Coursera workspace from
crashing, we've extracted a subset of the embeddings for the words that you'll
use in this assignment.

If you want to run this on your local computer and use the full dataset,
you can download the
* English embeddings from Google code archive word2vec
[look for GoogleNews-vectors-negative300.bin.gz](https://code.google.com/archive/p/word2vec/)
    * You'll need to unzip the file first.
* and the French embeddings from
[cross_lingual_text_classification](https://github.com/vjstark/crosslingual_text_classification).
    * in the terminal, type (in one line)
    `curl -o ./wiki.multi.fr.vec https://dl.fbaipublicfiles.com/arrival/vectors/wiki.multi.fr.vec`

Then copy-paste the code below and run it.

```python
# Use this code to download and process the full dataset on your local computer

from gensim.models import KeyedVectors

en_embeddings = KeyedVectors.load_word2vec_format('./GoogleNews-vectors-negative300.bin', binary = True)
fr_embeddings = KeyedVectors.load_word2vec_format('./wiki.multi.fr.vec')


# loading the english to french dictionaries
en_fr_train = get_dict('en-fr.train.txt')
print('The length of the english to french training dictionary is', len(en_fr_train))
en_fr_test = get_dict('en-fr.test.txt')
print('The length of the english to french test dictionary is', len(en_fr_train))

english_set = set(en_embeddings.vocab)
french_set = set(fr_embeddings.vocab)
en_embeddings_subset = {}
fr_embeddings_subset = {}
french_words = set(en_fr_train.values())

for en_word in en_fr_train.keys():
    fr_word = en_fr_train[en_word]
    if fr_word in french_set and en_word in english_set:
        en_embeddings_subset[en_word] = en_embeddings[en_word]
        fr_embeddings_subset[fr_word] = fr_embeddings[fr_word]


for en_word in en_fr_test.keys():
    fr_word = en_fr_test[en_word]
    if fr_word in french_set and en_word in english_set:
        en_embeddings_subset[en_word] = en_embeddings[en_word]
        fr_embeddings_subset[fr_word] = fr_embeddings[fr_word]


pickle.dump( en_embeddings_subset, open( "en_embeddings.p", "wb" ) )
pickle.dump( fr_embeddings_subset, open( "fr_embeddings.p", "wb" ) )
```

the subset of data

In [106]:
en_embeddings_subset = pickle.load(open("data/en_embeddings.p", "rb"))
fr_embeddings_subset = pickle.load(open("data/fr_embeddings.p", "rb"))

In [107]:
print(en_embeddings_subset['the'][:10])
print(fr_embeddings_subset['la'][:10])

[ 0.08007812  0.10498047  0.04980469  0.0534668  -0.06738281 -0.12060547
  0.03515625 -0.11865234  0.04394531  0.03015137]
[-0.0061825  -0.00094387 -0.00882648  0.0324623  -0.0218281   0.0298912
  0.022999    0.0280628   0.00587757 -0.0256806 ]


In [108]:
# loading the english to french dictionaries
en_fr_train = get_dict('data/en-fr.train.txt')
print("The length of en fr training dataset: ", len(en_fr_train))
en_fr_test = get_dict('data/en-fr.test.txt')
print("The length of en fr test dataset: ", len(en_fr_test))

The length of en fr training dataset:  5000
The length of en fr test dataset:  1500


In [109]:
keys = ['the', 'and', 'was', 'for']
values = [en_fr_train[k] for k in keys]
print(dict(zip(keys, values)))


{'the': 'la', 'and': 'et', 'was': 'était', 'for': 'pour'}


## 1.1 Generate embedding and transform matrices

Exercise 01: translating english dictionary to french by using embeddings

You will now implement a function `get_matrices`, which takes the loaded data
and returns matrices `X` and `Y`.

Inputs:
- `en_fr` : English to French dictionary
- `en_embeddings` : English to embeddings dictionary
- `fr_embeddings` : French to embeddings dictionary

Returns:
- Matrix `X` and matrix `Y`, where each row in X is the word embedding for an
english word, and the same row in Y is the word embedding for the French
version of that English word.

In [110]:
fr_embeddings_subset

{'la': array([-6.18250e-03, -9.43867e-04, -8.82648e-03,  3.24623e-02,
        -2.18281e-02,  2.98912e-02,  2.29990e-02,  2.80628e-02,
         5.87757e-03, -2.56806e-02,  4.21732e-02, -9.37519e-03,
         2.86577e-02, -5.08309e-02, -7.13388e-02, -8.34270e-03,
        -2.88709e-02, -3.85773e-02,  4.38649e-02,  1.18239e-01,
        -8.57782e-02,  2.65617e-02, -1.21373e-01, -1.88254e-02,
        -5.46811e-02, -8.06788e-02,  3.16896e-02, -3.78146e-02,
         4.16330e-02, -3.09924e-02, -4.15530e-02,  5.95500e-02,
        -6.08129e-02,  1.29453e-01,  5.98485e-02, -1.22053e-01,
        -4.65893e-02, -1.76105e-02,  8.36952e-02, -3.43169e-02,
         1.02949e-02, -3.74583e-02,  1.56218e-02,  2.52615e-02,
         3.09000e-02, -6.15672e-03,  1.78421e-02, -7.97611e-03,
         4.08416e-02, -3.61498e-02,  5.93975e-02, -6.13706e-02,
         2.76527e-02, -4.04968e-02,  4.02123e-02,  4.60480e-02,
         3.12373e-02,  4.31485e-02,  4.45423e-03,  9.88624e-05,
        -3.46425e-03, -7.78974e-02

In [111]:
def get_matrices(en_fr, french_vecs, english_vecs):
  """
  input
    en_fr: english to french dictionary
    french_vecs: french words to their corresponding word embeddings
    english_vecs: english words to their corresponding word embeddings
  output
    X: english embeddings matrix
    Y: french embeddings matrix
    R: the projection matrix that minimizes the F norm ||X R - Y||^2
  """

  # X_1 and Y_1 are lists of the english and french word embeddings
  X_1 = list()
  Y_1 = list()

  # get the english words, french words
  english_set = set(english_vecs.keys())
  french_set = set(french_vecs.keys())

  # store french in dictionary
  french_words = set(en_fr.values())

  # loop through all english, french word pairs in dictionary
  for en_word, fr_word in en_fr.items():
    if fr_word in french_set and en_word in english_set:
      en_vec = english_vecs[en_word]
      fr_vec = french_vecs[fr_word]
      X_1.append(en_vec)
      Y_1.append(fr_vec)
  X = np.array(X_1)
  Y = np.array(Y_1)

  return X, Y

In [112]:
X_train, Y_train = get_matrices(en_fr_train, fr_embeddings_subset, en_embeddings_subset)

In [113]:
X_train, Y_train

(array([[ 0.08007812,  0.10498047,  0.04980469, ...,  0.00366211,
          0.04760742, -0.06884766],
        [ 0.02600098, -0.00189209,  0.18554688, ..., -0.12158203,
          0.22167969, -0.02197266],
        [-0.01177979, -0.04736328,  0.04467773, ...,  0.07128906,
         -0.03491211,  0.02416992],
        ...,
        [-0.17089844,  0.17871094, -0.06494141, ..., -0.10644531,
         -0.31640625, -0.09326172],
        [-0.21875   ,  0.09179688,  0.03637695, ..., -0.015625  ,
         -0.27148438,  0.14941406],
        [-0.00418091,  0.0703125 , -0.04516602, ..., -0.16015625,
          0.09326172, -0.15039062]], dtype=float32),
 array([[-0.0061825 , -0.00094387, -0.00882648, ...,  0.111644  ,
         -0.0503964 , -0.0603421 ],
        [-0.0341354 ,  0.042414  , -0.0656882 , ..., -0.0539992 ,
          0.0371097 , -0.0433599 ],
        [ 0.0426481 ,  0.0395683 , -0.00825683, ...,  0.0295259 ,
          0.0713421 ,  0.0626402 ],
        ...,
        [ 0.0903279 , -0.108363  , -0.0

# 2. Translation

## 2.1 Translation as linear transformation of embeddings

### Describing translation as the minimization problem

Find a matrix `R` that minimizes the following equation. 

$$\arg \min _{\mathbf{R}}\| \mathbf{X R} - \mathbf{Y}\|_{F}\tag{1} $$

### Frobenius norm

The Frobenius norm of a matrix $A$ (assuming it is of dimension $m,n$) is defined as the square root of the sum of the absolute squares of its elements:

$$\|\mathbf{A}\|_{F} \equiv \sqrt{\sum_{i=1}^{m} \sum_{j=1}^{n}\left|a_{i j}\right|^{2}}\tag{2}$$

### Actual loss function
In the real world applications, the Frobenius norm loss:

$$\| \mathbf{XR} - \mathbf{Y}\|_{F}$$

is often replaced by it's squared value divided by $m$:

$$ \frac{1}{m} \|  \mathbf{X R} - \mathbf{Y} \|_{F}^{2}$$

where $m$ is the number of examples (rows in $\mathbf{X}$).

* The same R is found when using this loss function versus the original Frobenius norm.
* The reason for taking the square is that it's easier to compute the gradient of the squared Frobenius.
* The reason for dividing by $m$ is that we're more interested in the average loss per embedding than the  loss for the entire training set.
    * The loss for all training set increases with more words (training examples),
    so taking the average helps us to track the average loss regardless of the size of the training set.

### Exercise 02: Implementing translation mechanism described in this section.

#### Step 1: Computing the loss
* The loss function will be squared Frobenoius norm of the difference between
matrix and its approximation, divided by the number of training examples $m$.
* Its formula is:
$$ L(X, Y, R)=\frac{1}{m}\sum_{i=1}^{m} \sum_{j=1}^{n}\left( a_{i j} \right)^{2}$$

where $a_{i j}$ is value in $i$th row and $j$th column of the matrix $\mathbf{XR}-\mathbf{Y}$.

#### Instructions: complete the `compute_loss()` function

* Compute the approximation of `Y` by matrix multiplying `X` and `R`
* Compute difference `XR - Y`
* Compute the squared Frobenius norm of the difference and divide it by $m$.



In [114]:
def compute_loss(X, Y, R):
  '''
  input
    X: english embeddings (m,n) -- m*300
    Y: french embeddings (m,n) -- m*300
    R: transformation matrix (n,n) -- 300*300
  output
    L: the value of the loss function (m,n)
  '''
  m = X.shape[0]
  diff = np.dot(X, R) - Y
  diff_squared = diff**2
  sum_diff_squared = np.sum(diff_squared)
  loss = sum_diff_squared/m

  return loss

### Step 2: Computing the gradient of loss in respect to transform matrix R

* Calculate the gradient of the loss with respect to transform matrix `R`.
* The gradient is a matrix that encodes how much a small change in `R`
affect the change in the loss function.
* The gradient gives us the direction in which we should decrease `R`
to minimize the loss.
* $m$ is the number of training examples (number of rows in $X$).
* The formula for the gradient of the loss function $𝐿(𝑋,𝑌,𝑅)$ is:

$$\frac{d}{dR}𝐿(𝑋,𝑌,𝑅)=\frac{d}{dR}\Big(\frac{1}{m}\| X R -Y\|_{F}^{2}\Big) = \frac{2}{m}X^{T} (X R - Y)$$

**Instructions**: Complete the `compute_gradient` function below.

In [115]:
# UNQ_C4 (UNIQUE CELL IDENTIFIER, DO NOT EDIT)
def compute_gradient(X, Y, R):
    '''
    Inputs: 
        X: a matrix of dimension (m,n) where the columns are the English embeddings.
        Y: a matrix of dimension (m,n) where the columns correspong to the French embeddings.
        R: a matrix of dimension (n,n) - transformation matrix from English to French vector space embeddings.
    Outputs:
        g: a matrix of dimension (n,n) - gradient of the loss function L for given X, Y and R.
    '''
    ### START CODE HERE (REPLACE INSTANCES OF 'None' with your code) ###
    # m is the number of rows in X
    m = X.shape[0]

    # gradient is X^T(XR - Y) * 2/m
    gradient = (2/m)*np.dot(X.T, (np.dot(X,R)-Y))
    ### END CODE HERE ###
    return gradient


### Step 3: Finding the optimal R with gradient descent algorithm

Pseudocode:
1. Calculate gradient $g$ of the loss with respect to the matrix $R$.
2. Update $R$ with the formula:
$$R_{\text{new}}= R_{\text{old}}-\alpha g$$

Where $\alpha$ is the learning rate, which is a scalar.

## Exercise 04

In [121]:
def align_embeddings(X, Y, train_steps=100, learning_rate=0.0003):
    '''
    Inputs:
        X: a matrix of dimension (m,n) where the columns are the English embeddings.
        Y: a matrix of dimension (m,n) where the columns correspong to the French embeddings.
        train_steps: positive int - describes how many steps will gradient descent algorithm do.
        learning_rate: positive float - describes how big steps will  gradient descent algorithm do.
    Outputs:
        R: a matrix of dimension (n,n) - the projection matrix that minimizes the F norm ||X R -Y||^2
    '''
    np.random.seed(129)

    # the number of columns in X is the number of dimensions for a word vector (e.g. 300)
    # R is a square matrix with length equal to the number of dimensions in th  word embedding
    R = np.random.rand(X.shape[1], X.shape[1])
    # print(R)
    for i in range(train_steps):
        if i % 25 == 0:
            print(f"loss at iteration {i} is: {compute_loss(X, Y, R):.4f}")
        ### START CODE HERE (REPLACE INSTANCES OF 'None' with your code) ###
        # use the function that you defined to compute the gradient
        gradient = compute_gradient(X,Y,R)
        # print(gradient)
        # print(gradient)
        # print(gradient.shape)
        # update R by subtracting the learning rate times gradient
        R -= learning_rate*gradient
        ### END CODE HERE ###
    return R

In [122]:
np.random.seed(129)
m = 10
n = 5
X = np.random.rand(m, n)
Y = np.random.rand(m, n) * .1

# gradient = compute_gradient(X,Y,R)
# print(X.shape)
# print(gradient.shape)
# print(R.shape)

R = align_embeddings(X, Y)

loss at iteration 0 is: 3.7242
loss at iteration 25 is: 3.6283
loss at iteration 50 is: 3.5350
loss at iteration 75 is: 3.4442


# Calculate transformation matrix R

In [123]:
R_train = align_embeddings(X_train, Y_train, train_steps=400, learning_rate=0.8)

loss at iteration 0 is: 963.0146
loss at iteration 25 is: 97.8292
loss at iteration 50 is: 26.8329
loss at iteration 75 is: 9.7893
loss at iteration 100 is: 4.3776
loss at iteration 125 is: 2.3281
loss at iteration 150 is: 1.4480
loss at iteration 175 is: 1.0338
loss at iteration 200 is: 0.8251
loss at iteration 225 is: 0.7145
loss at iteration 250 is: 0.6534
loss at iteration 275 is: 0.6185
loss at iteration 300 is: 0.5981
loss at iteration 325 is: 0.5858
loss at iteration 350 is: 0.5782
loss at iteration 375 is: 0.5735


<a name="2-2"></a>

## 2.2 Testing the translation

### k-Nearest neighbors algorithm

[k-Nearest neighbors algorithm](https://en.wikipedia.org/wiki/K-nearest_neighbors_algorithm) 
* k-NN is a method which takes a vector as input and finds the other vectors in the dataset that are closest to it. 
* The 'k' is the number of "nearest neighbors" to find (e.g. k=2 finds the closest two neighbors).

### Searching for the translation embedding
Since we're approximating the translation function from English to French embeddings by a linear transformation matrix $\mathbf{R}$, most of the time we won't get the exact embedding of a French word when we transform embedding $\mathbf{e}$ of some particular English word into the French embedding space. 
* This is where $k$-NN becomes really useful! By using $1$-NN with $\mathbf{eR}$ as input, we can search for an embedding $\mathbf{f}$ (as a row) in the matrix $\mathbf{Y}$ which is the closest to the transformed vector $\mathbf{eR}$

### Cosine similarity
Cosine similarity between vectors $u$ and $v$ calculated as the cosine of the angle between them.
The formula is 

$$\cos(u,v)=\frac{u\cdot v}{\left\|u\right\|\left\|v\right\|}$$

* $\cos(u,v)$ = $1$ when $u$ and $v$ lie on the same line and have the same direction.
* $\cos(u,v)$ is $-1$ when they have exactly opposite directions.
* $\cos(u,v)$ is $0$ when the vectors are orthogonal (perpendicular) to each other.

#### Note: Distance and similarity are pretty much opposite things.
* We can obtain distance metric from cosine similarity, but the cosine similarity can't be used directly as the distance metric. 
* When the cosine similarity increases (towards $1$), the "distance" between the two vectors decreases (towards $0$). 
* We can define the cosine distance between $u$ and $v$ as
$$d_{\text{cos}}(u,v)=1-\cos(u,v)$$

In [163]:
def nearest_neighbor(v, candidates, k=1):
  """
  input:
    v
    candidates
    k
  output:
    k_idx: the indices of the top k closest vectors in sorted form
  """
  similarity_1 = []

  # for each candidate vector
  for row in candidates:
    con_similarity = cosine_similarity(v, row)
    similarity_1.append(con_similarity)

  sorted_ids = np.argsort(np.array(similarity_1))
  print(sorted_ids)
  k_idx = sorted_ids[:k]

  return k_idx

In [165]:
# UNQ_C9 (UNIQUE CELL IDENTIFIER, DO NOT EDIT)
# You do not have to input any code in this cell, but it is relevant to grading, so please do not change anything

# Test your implementation:
v = np.array([1, 0, 1])
candidates = np.array([[1, 0, 5], [-2, 5, 3], [2, 0, 1], [6, -9, 5], [9, 9, 9]])
# nearest_neighbor(v, candidates, 3)
print(candidates[nearest_neighbor(v, candidates, 3)])

[1 3 4 0 2]
[[-2  5  3]
 [ 6 -9  5]
 [ 9  9  9]]


In [168]:
candidates

array([[ 1,  0,  5],
       [-2,  5,  3],
       [ 2,  0,  1],
       [ 6, -9,  5],
       [ 9,  9,  9]])